In [1]:
import undetected_chromedriver
import time
import re
import random
# from datetime import datetime, date, time, timedelta
import pickle
import requests
from requests.auth import HTTPBasicAuth
import numpy as np
import pandas as pd
import pandas as pd
from bs4 import BeautifulSoup
from tqdm import tqdm
import warnings
warnings.filterwarnings("ignore")

In [2]:
from dataclasses import asdict

from selenium.webdriver.common.by import By
from selenium.common.exceptions import NoSuchElementException
from selenium.webdriver.common.keys import Keys 

# from dataclasses import dataclass
# from typing import Union

# @dataclass
# class Filial:
#     link: str
#     address: str

In [195]:
class Russian_romanizer(object):

    """преобразует русское название города в латиницу,
    чтобы передать в запрос yandex api по организациям"""
    cyrillic = {
        u'\u0401': u'YO',
        u'\u0410': u'a',
        u'\u0411': u'B',
        u'\u0412': u'V',
        u'\u0413': u'G',
        u'\u0414': u'D',
        u'\u0415': u'E',
        u'\u0416': u'ZH',
        u'\u0417': u'Z',
        u'\u0418': u'I',
        u'\u0419': u'I',
        u'\u041a': u'K',
        u'\u041b': u'L',
        u'\u041c': u'M',
        u'\u041d': u'N',
        u'\u041e': u'O',
        u'\u041f': u'P',
        u'\u0420': u'R',
        u'\u0421': u'S',
        u'\u0422': u'T',
        u'\u0423': u'U',
        u'\u0424': u'F',
        u'\u0425': u'H',
        u'\u0426': u'TS',
        u'\u0427': u'CH',
        u'\u0428': u'SH',
        u'\u0429': u'SHCH',
        u'\u042a': u"",
        u'\u042b': u'I',
        u'\u042c': u"", 
        u'\u042d': u'E',
        u'\u042e': u'YU',
        u'\u042f': u'YA',
        u'\u0430': u'a',
        u'\u0431': u'b',
        u'\u0432': u'v',
        u'\u0433': u'g',
        u'\u0434': u'd',
        u'\u0435': u'e', 
        u'\u0436': u'zh',
        u'\u0437': u'z',
        u'\u0438': u'i',
        u'\u0439': u'y', # 
        u'\u043a': u'k',
        u'\u043b': u'l',
        u'\u043c': u'm',
        u'\u043d': u'n',
        u'\u043e': u'o',
        u'\u043f': u'p',
        u'\u0440': u'r',
        u'\u0441': u's',
        u'\u0442': u't',
        u'\u0443': u'u',
        u'\u0444': u'f',
        u'\u0445': u'kh', 
        u'\u0446': u'ts',
        u'\u0447': u'ch',
        u'\u0448': u'sh',
        u'\u0449': u'shch',
        u'\u044a': u"", 
        u'\u044b': u'y',
        u'\u044c': u"y", 
        u'\u044d': u'e', 
        u'\u044e': u'yu',
        u'\u044f': u'ya',
        u'\u0451': u'yo',
    }
    
    def __init__(self,txt):
        self.txt = txt
        
    def from_cyrillic(self,char):
        if char in self.cyrillic:
            return self.cyrillic[char]
        else:
            return char
        
    def transliterate(self):
        return ''.join([self.from_cyrillic(val) for val in self.txt])

from difflib import SequenceMatcher


def similar(a, b):
    """рассчитывает сходство между строками a и b"""
    return SequenceMatcher(None, a, b).ratio()

def custom_handle(roman_city):
    if roman_city.startswith('novyi') and ' ' in roman_city:
        roman_city = roman_city.split(' ')[1]
    ended = ['nyy', 'goi', 'nyi', 'koi', 'kiy', 'kyy', 'noe', 'goy']
    if roman_city[-3:] in ended:
        roman_city = roman_city[:-2]
    return roman_city

In [196]:
# 'moskva' = moscow
# almetevsk - almetyevsk
# vyazma - vyazma

# Мирный Новый Уренгой
# петергоф

In [199]:
city_name = 'Заволжье' 
city_name = city_name.lower()

In [183]:
params = dict(
text=f'альфа банк {city_name}',
type='biz',
lang='en_US',
apikey='cec67fc0-be48-435f-984d-b2f778a24fc0'
)
url = 'https://search-maps.yandex.ru/v1/'
resp = requests.get(url=url, params=params)
data = resp.json()

In [200]:
rom = Russian_romanizer(city_name)
roman_city = rom.transliterate()
roman_city = custom_handle(roman_city)
roman_city

'zavolzhye'

In [190]:
address = data['features'][0]['properties']['CompanyMetaData']['address'].lower()
address

'nizhniy novgorod region, gorodetskiy munitsipalny okrug, zavolzhye, ulitsa ponomaryova, 4'

In [191]:
roman_city in address

True

In [193]:
bool(re.search(roman_city, address))

True

In [187]:
similar(roman_city, address)

0.1836734693877551

In [271]:
with open('/Users/anyarulina/yandex-info-reviews-parser/cities_dict_alfa_bank.pickle', 'rb') as f:
    cities_dict_alfa_bank = pickle.load(f)
cities_dict_alfa_bank[city_name]

0

In [294]:
data['features'][0]['properties']['CompanyMetaData']['id']

'194526712498'

In [190]:
from difflib import SequenceMatcher

def similar(a, b):
    return SequenceMatcher(None, a, b).ratio()


In [20]:
0.3

'irkutsk region, cheremkhovo, pervomayskaya ulitsa, 160б'

In [4]:
def find_between(s, first, last):
    try:
        regex = rf'{first}(.*?){last}'
        return re.findall(regex, s)
    except ValueError:
        return -1


def get_id_from_page(page, print_links=False):

    first = 'search-snippet-view__link-overlay _focusable" href="/maps/org/bank_vtb/'
    last = '/" tabindex="'
    yndx_idx = find_between(page, first, last)

    print(f'founded {len(yndx_idx)} ids')
    
    if print_links:
    # full_links = []
        main_url = 'https://yandex.ru/maps/org/bank_vtb/'
        for l in yndx_idx:
            # full_links.append(main_url + l)
            print(main_url + l)

    return yndx_idx
    

def __scroll_to_bottom(elem, t):
    """
    Скроллим список до последнего отзыва
    :param elem: Последний отзыв в списке
    :param driver: Драйвер undetected_chromedriver
    :return: None
    """
    driver.execute_script(
        "arguments[0].scrollIntoView();",
        elem
    )
    # time.sleep(1)
    new_elem = driver.find_elements(By.CLASS_NAME, t)[-1]
    print('I scroll')
    if elem == new_elem:
        return
    __scroll_to_bottom(new_elem)

In [13]:
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from selenium.webdriver.common.by import By

opts = undetected_chromedriver.ChromeOptions()
opts.add_argument('--no-sandbox')
opts.add_argument('--disable-dev-shm-usage')
opts.add_argument('headless')
# opts.add_argument("--window-size=1366,768")
opts.add_argument('--disable-gpu')
driver = undetected_chromedriver.Chrome(options=opts)

driver.get("https://yandex.ru/maps/org/sberbank/1127148321/reviews")

# print(driver.page_source)

business_aspect = []

soup_content = BeautifulSoup(driver.page_source, "lxml")
# t = 'business-aspect-view__text'
for data in soup_content.find_all("div", ):
    address = data.getText()
    business_aspect.append(address)



driver.close()
driver.quit() 

In [32]:
def find_between(s, first, last):
    """находит строку между символами first и last"""
    try:
        regex = rf'{first}(.*?){last}'
        return re.findall(regex, s)
    except ValueError:
        return -1

def handle_business_aspect(business_aspect):
    d = {}

    for aspect in business_aspect:
        k = find_between(aspect, '', ' • ')[0]
        v = find_between(aspect, ' • ', '%')[0]
        d[k] = v
    return d

In [37]:
d

{'Обслуживание': '90',
 'Персонал': '84',
 'Отношение к клиентам': '85',
 'Время ожидания': '80',
 'Банкомат': '73'}

In [5]:
def get_yndx_id_from_chain(yndx_bank_id):
    
    opts = undetected_chromedriver.ChromeOptions()
    opts.add_argument('--no-sandbox')
    opts.add_argument('--disable-dev-shm-usage')
    opts.add_argument('headless')
    opts.add_argument('--disable-gpu')
    driver = undetected_chromedriver.Chrome(options=opts)
    
    # TODO: для разных банков - name == sberbank
    # bank_name = 'bank_vtb'
    # url = f'https://yandex.ru/maps/org/{bank_name}/{yndx_bank_id}/chain/'
    url = f'https://yandex.ru/maps/org/sberbank/{yndx_bank_id}/chain/'
    driver.get(url)
    
    t = 'business-tab-wrapper' 
    elements = driver.find_elements(By.CLASS_NAME, t)
    
    # может работать не с 1ого раза
    if len(elements) > 1:

        # без этого не работает
        elements = driver.find_elements(By.CLASS_NAME, t)
    
        seen = []
    
        while True:
            driver.execute_script("arguments[0].scrollIntoView();", elements[-1]);
            # TODO: подольше спать?
            time.sleep(round(random.uniform(230.1, 239.9), 2))
            elements = driver.find_elements(By.CLASS_NAME, t)
            if len(elements) < 1:
                time.sleep(round(random.uniform(10.1, 19.9), 2))
    
            page3 = elements[3].get_attribute('innerHTML')
            yndx_idx = get_id_from_page(page3)
            
            last_size = len(yndx_idx)
            seen.append(last_size)
            
            # TODO: проверить, всё ли сохраняется?
            if len(set(seen))-1 < len(seen):
                break
    
    else:
        print('driver stopped')
        driver.close()
        driver.quit()
        
    driver.close()
    driver.quit() 
    
    return yndx_idx

In [ ]:
bank_name = 'alfa_bank'
yndx_bank_id = 89484726721

opts = undetected_chromedriver.ChromeOptions()
opts.add_argument('--no-sandbox')
opts.add_argument('--disable-dev-shm-usage')
opts.add_argument('headless')
opts.add_argument('--disable-gpu')
driver = undetected_chromedriver.Chrome(options=opts)

url = f'https://yandex.ru/maps/org/{bank_name}/{yndx_bank_id}/chain/'
driver.get(url)

t = 'business-tab-wrapper' 
elements = driver.find_elements(By.CLASS_NAME, t)

# может работать не с 1ого раза
if len(elements) > 1:

    # без этого не работает
    elements = driver.find_elements(By.CLASS_NAME, t)

    seen = []

    while True:
        driver.execute_script("arguments[0].scrollIntoView();", elements[-1]);

        # time.sleep(round(random.uniform(230.1, 239.9), 2))
        elements = driver.find_elements(By.CLASS_NAME, t)
        if len(elements) < 1:
            print('len < 1')
            time.sleep(round(random.uniform(10.1, 19.9), 2))
    
        page3 = elements[3].get_attribute('innerHTML')
        print(page3)
        yndx_idx = get_id_from_page(page3)
        
        # last_size = len(yndx_idx)
        # seen.append(last_size)
        
        # # TODO: проверить, всё ли сохраняется?
        # if len(set(seen))-1 < len(seen):
        #     break

<div class="business-tab-wrapper__content"><div><div data-chunk="chain" data-ssr-uid="6-1"><div class="card-businesses-list"><div class="card-businesses-list__list"><div data-chunk="search-snippet" data-ssr-uid="6-2-1"></div></div></div></div></div></div>
founded 0 ids
<div class="business-tab-wrapper__content"><div><div data-chunk="chain" data-ssr-uid="6-1"><div class="card-businesses-list"><div class="card-businesses-list__list"><div data-chunk="search-snippet" data-ssr-uid="6-2-1"><li class="search-snippet-view"><div class="search-snippet-view__body _type_business _wide" data-object="search-list-item" data-id="89484726721" data-log-id="dHlwZT1iaXpmaW5kZXI7aWQ9ODk0ODQ3MjY3MjE=" data-coordinates="53.815067,56.475610"><div><span><!--noindex--></span><span data-nosnippet="true"><a class="search-snippet-view__link-overlay _focusable" href="/maps/org/alfa_bank/89484726721/" tabindex="-1" aria-label="Альфа-Банк">Альфа-Банк</a></span><span><!--/noindex--></span><div class="search-business-s

In [21]:
# fake_links = '/Users/anyarulina/Downloads/links_sberbank/sberbank/link_Fake.pkl'
check_links = '/Users/anyarulina/yandex-info-reviews-parser/check_link_1011010028.pkl'

with open(check_links, 'rb') as handle:
    check_links = pickle.load(handle)
check_links = ['https://yandex.ru/maps/org/sberbank/' + c for c in check_links]
check_links[2]

'https://yandex.ru/maps/org/sberbank/1128554212'

In [22]:
msk_links = '/Users/anyarulina/Downloads/links_sberbank/sberbank/link_Moskva.pkl'

with open(msk_links, 'rb') as handle:
    msk_links = pickle.load(handle)
len(msk_links)

23

In [23]:
set(msk_links).difference(set(check_links))

set()

In [24]:
set(check_links).difference(set(msk_links))

set()

In [4]:
# t = 'business-reviews-card-view__review'
# t = 'search-snippet-view__body _type_business _wide'
# t = 'search-business-snippet-view__content'
# t = 'search-business-snippet-view__sequence' # +-
# t = 'business-tab-wrapper__content' # +++++
# t = 'search-business-snippet-view__address' -
t = 'business-tab-wrapper' # +++++ 25 address
# t = 'business-tab-wrapper__content'
# t = 'search-snippet-view__body _type_business _wide'
# t = 'search-snippet'
# t = 'search-snippet-view'
# t = 'business-tab-wrapper__content' # +
# t = 'card-businesses-list__list'
# t = 'card-businesses-list'

# t = 'business-tab-wrapper _materialized' 
# <div data-chunk="search-snippet"

# t = 'sidebar-container'

In [113]:
def get_vtb_id_from_chain(vtb_bank_id):
    
    opts = undetected_chromedriver.ChromeOptions()
    opts.add_argument('--no-sandbox')
    opts.add_argument('--disable-dev-shm-usage')
    opts.add_argument('headless')
    opts.add_argument('--disable-gpu')
    driver = undetected_chromedriver.Chrome(options=opts)
    
    url = f'https://yandex.ru/maps/org/bank_vtb/{vtb_bank_id}/chain/'
    driver.get(url)
    
    t = 'business-tab-wrapper' 
    elements = driver.find_elements(By.CLASS_NAME, t)
    
    # может работать не с 1ого раза
    if len(elements) > 1:
    
        # без этого не работает
        elements = driver.find_elements(By.CLASS_NAME, t)
    
        seen = []
    
        while True:
            driver.execute_script("arguments[0].scrollIntoView();", elements[-1]);
            # TODO: подольше спать?
            time.sleep(5)
            elements = driver.find_elements(By.CLASS_NAME, t)
            if len(elements) < 1:
                time.sleep(5)
    
            page3 = elements[3].get_attribute('innerHTML')
            yndx_idx = get_id_from_page(page3)
            
            last_size = len(yndx_idx)
            seen.append(last_size)
            
            if len(set(seen)) < len(seen):
                print('I finished')
                break
    
    else:
        print('driver stopped')
        driver.close()
        driver.quit()
        
    driver.close()
    driver.quit() 
    
    return yndx_idx

In [114]:
yndx_idx = get_vtb_id_from_chain(119121952644)

founded 25 ids
founded 50 ids
founded 75 ids


KeyboardInterrupt: 

In [11]:
print(yndx_idx)

['108842531028', '115970153357', '58126187224', '1269903998', '1065477601', '235337541767', '1494695036', '1018823642', '4591086156', '220673277256', '1010681681', '1081597905', '112742912522', '117095934626', '29783571280', '1437293025', '27133499164', '1130286215', '1033745759', '1327391199', '7128644451', '65217920821', '1319804464', '1070033100', '72023112309', '11536838795', '1255057274', '25664524981', '1057066856', '74709651787', '1086135893', '154867663938', '17240174828', '1420832132', '1270083581', '1531857223', '1073336641', '1759951598', '57803806217', '1394732712', '21763314314', '1096076218', '186437166625', '120349263024', '1310673410', '1059995666', '1060668956', '182810389580', '1218613928', '35412070788', '37012281512', '1662536963', '1099217561', '83314062840', '1275504150', '32289656542', '137237435722', '1243081137', '1214808353', '1320953515', '1508412341', '149052401015', '44940801987', '90150627438', '226682227522', '68953039594', '1503457777', '1510939541', '11

In [ ]:
t = 'business-reviews-card-view__review'

class MyParser:
    def __init__(self, driver):
        self.driver = driver

    def __scroll_to_bottom(self, elem) -> None:
        """
        Скроллим список до последнего отзыва
        :param elem: Последний отзыв в списке
        :param driver: Драйвер undetected_chromedriver
        :return: None
        """
        self.driver.execute_script(
            "arguments[0].scrollIntoView();",
            elem
        )
        time.sleep(1)
        new_elem = self.driver.find_elements(By.CLASS_NAME, t)[-1]
        # new_elem = driver.find_elements(By.TAG_NAME, "a")[-1]
        print('I scroll')
        if elem == new_elem:
            return
        self.__scroll_to_bottom(new_elem)
        

    def __get_data_item(self, elem):
        """
        Спарсить данные по отзыву
        :param elem: Отзыв из списка
        :return: Словарь
        {
            name: str
            icon_href: Union[str, None]
            date: float
            text: str
            stars: float
        }
        """

        # try:
        #     link = elem.find_element(By.XPATH, ".//meta[@property='al:ios:url']").get_attribute('content')
        # except NoSuchElementException:
        #     print("no LINK")
        #     link = None

        try:
            link = elem.find_element(By.XPATH, ".//meta[@itemprop='datePublished']").get_attribute('content')
        except NoSuchElementException:
            link = None

        # try:
        #     link = elem.find_element(By.XPATH, ".//meta[@property='al:ios:url']").get_attribute('content')
        # except NoSuchElementException:
        #     print("no LINK")
        #     link = None
        
        try:
            address = elem.find_element(By.XPATH, ".//a[@class='search-business-snippet-view__address']").get_attribute('href')
            # icon_href = icon_href.split('"')[1]
        except NoSuchElementException:
            print('no ADRESS')
            address = None

        print(f'link {link}')
        item = Filial(
            link=link,
            address=address
        )
        return asdict(item)



    def __get_data_reviews(self) -> list:
        reviews = []
    
        elements = self.driver.find_elements(By.CLASS_NAME, t)
        print('elements 1 ', elements)
        #  time.sleep(2)
        # element.click()
        if len(elements) > 0:
            print('find elements level 1 ', elements)
        else:
            1/0
        if len(elements) > 1:
            self.__scroll_to_bottom(elements[-1])
            elements = self.driver.find_elements(By.CLASS_NAME, t)
            print('elements 1 ', elements)
            if len(elements) > 0:
                print('find elements level 2 ', elements)
            for elem in elements:
                reviews.append(self.__get_data_item(elem))
        return reviews

    def __isinstance_page(self):
        try:
            xpath_name = ".//h1[@class='orgpage-header-view__header']"
            name = self.driver.find_element(By.XPATH, xpath_name).text
            return True
        except NoSuchElementException:
            return False

    def parse_all_data(self) -> dict:
        """
        Начинаем парсить данные.
        :return: Словарь данных
        {
             company_info:{
                    name: str
                    rating: float
                    count_rating: int
                    stars: float
            },
            company_reviews:[
                {
                  name: str
                  icon_href: str
                  date: timestamp
                  text: str
                  stars: float
                }
            ]
        }
        """
        if not self.__isinstance_page():
            return {'error': 'Страница не найдена'}
        return {'company_info': self.__get_data_campaign(), 'company_reviews': self.__get_data_reviews()}

    def parse_reviews(self) -> dict:
        """
        Начинаем парсить данные только отзывы.
        :return: Массив отзывов
        {
            company_reviews:[
                {
                  name: str
                  icon_href: str
                  date: timestamp
                  text: str
                  stars: float
                }
            ]
        }

        """
        if not self.__isinstance_page():
            return {'error': 'Страница не найдена'}
        return {'company_reviews': self.__get_data_reviews()}




class YandexParser2:
    def __init__(self, id_yandex: int):
        """
        @param id_yandex: ID Яндекс компании
        """
        self.id_yandex = id_yandex

    def __open_page(self):
        url = 'https://yandex.ru/maps/org/{}/reviews/'.format(str(self.id_yandex))
        # url = 'https://yandex.ru/maps/org/{}/chain/'.format(str(self.id_yandex))
        opts = undetected_chromedriver.ChromeOptions()
        opts.add_argument('--no-sandbox')
        opts.add_argument('--disable-dev-shm-usage')
        opts.add_argument('headless')
        opts.add_argument('--disable-gpu')
        driver = undetected_chromedriver.Chrome(options=opts)
        parser = MyParser(driver)
        driver.get(url)
        return parser

    def parse(self, type_parse: str = 'default') -> dict:
        """
        Функция получения данных в виде
        @param type_parse: Тип данных, принимает значения:
            default - получает все данные по аккаунту
            company - получает данные по компании
            reviews - получает данные по отчетам
        @return: Данные по запрошенному типу
        """
        result:dict = {}
        page = self.__open_page()
        time.sleep(4)
        try:
            if type_parse == 'default':
                result = page.parse_all_data()
            if type_parse == 'company':
                result = page.parse_company_info()
            if type_parse == 'reviews':
                print('start get reviews')
                result = page.parse_reviews()
        except Exception as e:
            print('error: ', e)
            return result
        finally:
            page.driver.close()
            page.driver.quit()
            print('driver closed')
            return result


In [ ]:
# parser = YandexParser2(220673277256)

# reviews = parser.parse(type_parse='reviews')

In [ ]:
reviews

In [ ]:
# opts = undetected_chromedriver.ChromeOptions()
# opts.add_argument('--no-sandbox')
# opts.add_argument('--disable-dev-shm-usage')
# opts.add_argument('headless')
# opts.add_argument('--disable-gpu')
# driver = undetected_chromedriver.Chrome(options=opts)
#         # parser = Parser(driver)
# # url_com = 'https://yandex.ru/maps/org/bank_vtb/115970153357/chain/'
# url = 'https://yandex.ru/maps/org/115970153357/chain/'
# driver.get(url)  



# reviews = __get_data_reviews()

In [ ]:
# # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # 

In [ ]:
# search-business-snippet-view__content

# search-business-snippet-view__address

# search-business-snippet-view__sequence-item _priority_low

In [ ]:
t = 'business-urls-view__link'

In [ ]:
'business-urls-view__link'
'business-urls-view__url'
'business-tab-wrapper__content'
'.business-card-view__main-wrapper'
"business-card-view__awards"

'business-card-view__extend'

In [ ]:
# # # # # 